<img src="unicamp.png" width="150" height="150">

## MO444/MC886 - Aprendizado de Máquina e Reconhecimento de Padrões

Esse trabalho foi feito pelos seguintes membros:

- Lucas Zanco Ladeira - 188951
- Rafael Scherer - 204990 

O código original deste projeto está disponível no [repositório do Github](https://github.com/lucaslzl/mo444_p3_genref). 

## Algoritmos Evolutivos e Métodos de Aprendizado por Reforço

### Parte I - Algoritmos Evolutivos

<b>Declaração do problema</b><br>
"Nesta parte, seu grupo deve aplicar uma técnica de computação evolucionária para resolver o problema do Pac-man. O trabalho
consiste em encontrar uma solução adequada para o problema, avaliando-o segundo diversos parâmetros."

### Descrição

A interação entre o agente (pac-man) e o ambiente é feita utilizando a seguinte [ferramenta](http://cs.brynmawr.edu/Courses/cs372/fall2017/Code/search.zip.), com a versão para Python 3. É possível passar como parâmetro o agente a ser utilizado, sendo que, as possíveis ações do agente compreendem os movimentos a serem executados no jogo, sendo eles:
- North
- West
- East
- South
- Stop

A seguir está disponível a implementação do agente, o qual itera a lista de movimentos. Após o último elemento da lista a única ação feita é de <i>Stop</i>.

In [ ]:
from search.game import Agent, Directions


class SuperAgent(Agent):


    def __init__(self, moves=None):

        self.moves = moves
        self.iteration = 0


    def getAction(self, state):

        self.iteration += 1

        if  self.iteration < len(self.moves) and self.moves[self.iteration-1] in state.getLegalPacmanActions():
            return self.moves[self.iteration-1]
        else:
            return Directions.STOP

Para interagir com o ambiente e encontrar uma solução, foi escolhido utilizar um algoritmo genético. Considerando as características deste tipo de meta-heurística, agora iremos definir alguns parâmetros e estratégias implementadas.

<b>População</b>

A população é gerada aleatoriamente para explorar o conjunto de soluções possíveis. Cada gene da população compreende 200 movimentos do Pac-man. Portanto, o agente apenas faz alguma ação nos 200 primeiros movimentos, após isso o agente fica parado até que algum fantasma o encontre. O tamanho da população escolhido é de 100 genes. O código a seguir foi utilizado para gerar aleatoriamente os genes.

In [ ]:
import numpy as np

MOVES = [Directions.NORTH, Directions.EAST, Directions.SOUTH, Directions.WEST]

def generate_gene(size:int = 200):

    return np.random.choice(MOVES, size)


def generate_population(size:int = 100):

    population = []

    for i in range(size):
        population.append(generate_gene())
    
    return population

<b>Configuração da Ferramenta</b>

É possível utilizar a ferramenta de 2 maneiras, a) chamando o código pelo terminal e passando os parâmetros, b) importando as classes e chamando o método <i>runGames</i> da classe pacman. Escolhemos utilizar com a segunda opção. Sendo assim, para configurar a ferramenta é necessário gerar um dicionário com os parâmetros como é apresentado no código a seguir. É obtido o nome do layout a ser executado, o agente, são criados 4 fantasmas aleatórios, desligada a parte gráfica, entre outras configurações.

In [ ]:
def gen_args(layout_name, agent):

    args = {}

    args['layout'] = layout.getLayout(layout_name)
    args['pacman'] = agent
    args['ghosts'] = [RandomGhost(i+1) for i in range(4)]

    args['display'] = textDisplay.NullGraphics()
    args['numGames'] = 1
    args['record'] = False
    args['catchExceptions'] = False
    args['timeout'] = 1

    return args

<b>Função de <i>Fitness</i></b>

Com a população e o dicionário dos parâmetros é possível executar um jogo. Como utilizamos o score dado pela ferramenta, então a execução dos jogos se refere a nossa função <i>fitness</i> (com nome de evaluate no código). O código a seguir descreve a execução considerando cada membro da população e obtenção do score. É retornado apenas 1 score para cada membro da população e esse descreve o avanço do agente dada cada lista de movimentos.

In [ ]:
def evaluate(population, maze='tinyMaze'):
    
    scores = []

    for p in population:

        args = gen_args(maze, SuperAgent(p))
        games = runGames(**args)
        score = games[-1].state.getScore()
        scores.append(score)
    
    return scores

<b><i>Loop</i> Principal</b>

Definidas as funções de geração de população, configuração e <i>fitness</i>, agora será apresentado o <i>loop</i> principal e as funções que geram uma nova população a cada iteração. A função <i>run</i> recebe como parâmetro o nome do labirinto e qual é a iteração (quantidade de execuções do experimento) para gerar arquivos distintos. Primeiramente é gerada uma nova população e criado um dicionário para armazenar os resultados. Então, o loop é executado 100 vezes. A biblioteca <i>tqdm</i> cria uma barra de carregamento para ajudar a acompanhar a execução. A função <i>evaluate</i> já foi apresentada. A próxima função salva os scores no dicionário <i>history</i>. As próximas 4 funções fazem a seleção, crossover, mutação e replacement para gerar uma nova população. Por fim, após é obtido o melhor gene da última população e os resultados são salvos.

In [ ]:
def run(maze, iteration, pop_size):

    population = generate_population(pop_size)
    history = {
        'mini': [],
        'maxi': [],
        'mean': [],
        'scores': []
    }
    
    for i in tqdm(range(100)):

        scores = evaluate(population, maze)
        history = get_stats(history, scores)

        psel = select(population, scores)
        pcro = crossover(population)
        pmut = mutation(population)
        prep = replacement(population, psel, pcro, pmut)
        
        population = prep

    history['best'] = get_best(population, scores)
    save_history(history, maze, iteration)

<b>Select</b>

The select function has the goal to obtain the top <i>x</i> genes of the population according to the score. So, first <i>qty</i> stores how many elements should be selected. Then, we sort the list and select the elements.

In [ ]:
def select(population, scores):
    
    # Get how many elements will be selected
    qty = int(len(population)*BEST_RATE)
    
    # Get top qty elements from list
    # Ref: https://stackoverflow.com/questions/13070461/get-indices-of-the-top-n-values-of-a-list
    indexes = sorted(range(len(scores)), key=lambda i: scores[i], reverse=True)[:qty]
    selected = np.array(population)[indexes].tolist()

    return selected

<b>Crossover</b>

The crossover function has the goal to obtain the top <i>x</i> genes of the population according to the score and make crossover transformation. The crossover implemented selects pairs of genes and a split position to create new genes. A <i>new_x</i> gene comprehends the first gene of the pair from the start to the split position, and the second gene from the split position to the end. A <i>new_y</i> goes through the same transformation but it uses the second gene of the pair from the start to the split position and the first gene from the split position to the end of the gene. The crossover occurs $\frac{qty}{2}$ times. And generates <i>qty</i> new genes.

In [ ]:
def crossover(population):

    # Get how many elements will be selected
    qty = int(len(population)*CROSSOVER_RATE)

    crossed = []

    # Get two random elements and apply crossover
    for i in range(qty//2):

        # Get two random indexes
        x = random.randrange(len(population))
        y = random.randrange(len(population))

        # Get random genes
        x = population[x]
        y = population[y]

        # Get crossover split position
        split = random.randrange(len(x))
        new_x = np.array(x)[:split].tolist() + np.array(y)[split:].tolist()
        new_y = np.array(y)[:split].tolist() + np.array(x)[split:].tolist()

        crossed.append(new_x)
        crossed.append(new_y)

    return crossed

<b>Mutation</b>

The mutation function has the goal to obtain the top <i>x</i> genes of the population according to the score and make mutations. A mutation comprehends to select a random gene, select randomly a position of the gene, and change to a random move.

In [ ]:
def mutation(population):
    
    # Get how many elements will be selected
    qty = int(len(population)*MUTATION_RATE)

    mutated = []

    for i in range(qty):
        
        # Get a random index
        x = random.randrange(len(population))

        # Get random gene
        x = population[x]

        sel_move = np.random.choice(MOVES, 1)[0]
        sel_pos = random.randrange(len(x))

        x[sel_pos] = sel_move

        mutated.append(x)

    return mutated

<b>Replacement</b>

The replacement function has the goal to create the new population with the genes that were obtained from select, crossover and mutation. In addition, it adds randomly selected genes to fill the population until the size.

In [ ]:
def replacement(population, psel, pcro, pmut):
    
    replaced = []

    replaced.extend(psel)
    replaced.extend(pcro)
    replaced.extend(pmut)

    qty = int(len(population)*REPLACEMENT_RATE)
    rep = np.random.choice(len(population), qty)

    rep = np.array(population)[rep].tolist()

    replaced.extend(rep)

    return replaced

<b>Definições</b>

No enunciado do trabalho foi mencionada a necessidade de definir claramente algumas características da solução. Essas características e suas definições são:

- O modelo evolutivo adotado: algoritmo genético.
- Variações nos parâmetros: labirinto utilizado e tamanho da população.
- Função de Fitness adotada: score resultante dado pela ferramenta.
- Tamanho da população: 100 e 10.
- Critério de parada: até atingir o fim do jogo.
- Técnica de seleção: 40% genes mais bem avaliados.
- Técnica de crossover: corte na lista de ações e troca.
- Técnica de mutação: escolhe movimento aleatório e troca por outro.
- Método de replacement: 20% da população aleatoriamente.
- Taxa de mutação: 20%.
- Taxa de crossover: 20%.

### Metodologia

A solução utiliza o score da ferramenta para avaliar quão boa é a lista de movimento obtidos. Este score é positivo apenas se foi possível finalizar o jogo, senão, o score é negativo. Quão mais rápido for o gene, maior é o valor de score. O contrário também vale, quão menor o valor mais demorou o jogo.

A solução foi executada para populações de tamanho 10 e 100, com os seguintes labirintos e quantidades de iterações:

<b>10</b>
- smallClassic (10x)
- mediumClassic (10x)
- originalClassic (10x)


<b>100</b>
- smallClassic (10x)
- mediumClassic (3x)
- originalClassic (3x)

No caso da população com tamanho 100, como para os labirintos maiores a solução demora mais de 6 horas por iteração, elas foram executadas um menor número de vezes. Todavia, como a população é representativamente maior, o espaço de soluções é bastante explorado pela geração aleatória de genes. Todos os resultados obtidos foram salvos nas pastas <i>output_10</i> ou <i>output_100</i> de acordo com o tamanho da população.

Após a execução dos experimentos, o algoritmo <i>genplots.py</i> faz a leitura dos dados, os agrupa e calcula a média do score mínimo, médio e máximo de acordo com cada iteração. Não encontramos como obter da ferramenta o número de ações de cada gene, portanto, não será apresentado resultado para este dado.

### Resultados

Os resultados da estratégia implementada, comparam os valores de score mínimo, médio e máximo agregado das iterações de acordo com cada tamanho de população. Nas figuras a seguir podemos visualizar estes resultados.

<table><tr><td><img src='genetic_algorithm/plots/plot_10.png'></td><td><img src='genetic_algorithm/plots/plot_100.png'></td></tr></table>

Vemos que para população com 10 genes por geração existe uma variação menor nos resultados, além disso, não foi possível encontrar uma solução que pegasse todas as bolas. É possível observar que a diferença entre cada valor (mínimo, médio e máximo) é pequena comparado com o que é encontrado em 100. Essa características já era de se esperar por uma menor variação entre os genes. Ainda observando a figura da esquerda, tem-se uma diferença no labirinto e no score obtido, sendo que, para o menor labirinto (Smallclassic) foi possível atingir um score maior pois a quantidade de soluções é menor. Como a geração da população e os movimentos dos fantasmas são aleatórios existe uma probabilidade menor de obter um gene com bons resultados. Por fim, para até 100 iterações ainda não foi apresentado comportamento de crescimento no score obtido.

Podemos observar na figura da direita os resultados para população com 100 genes por geração, na qual, existe uma variação grande nos resultados. Existe um crescimento significativo entre o melhor gene inicial e o melhor gene da última geração. Geralmente não é observada tanta variação no melhor gene para soluções de algoritmos genéticos, sendo comumente observado um crescimento contínuo, ou pelo menos mantendo o valor obtido. Mas, a cada chamada para a ferramenta os movimentos dos fantasmas é distinto, o qual torna difícil para uma estratégia deste tipo por si só manter os resultados. Podemos observar que em todos os labirintos foi possível obter soluções onde o agente foi capaz de vencer o jogo. Isso mostra a importância de um pool genético com tamanho suficiente para explorar as possíveis soluções. Com até 30 gerações foi possível obter algum gene que venceu o jogo, sendo possível diminuir a quantidade de gerações pelo tamanho da população escolhido.

<b>Considerações Finais</b>

Foi possível observar a diferença nos resultados obtidos de acordo com o labirinto e tamanho da população. Vemos que o tamanho da população foi muito importante para atingir o resultado esperado. No entanto, pela aleatoriedade da ferramenta vemos que não é possível garantir uma solução única para todas as execuções. Uma estratégia que atualiza os movimentos de acordo com a experiência se torna necessária. Como trabalhos futuros gostaríamos de estender o trabalho para variar as taxas de crossover, mutação, e seleção dos melhores genes.

In [9]:
!cd rl_algorithm/search && python3 pacman.py -p QLearningAgent -x 30000 -n 30010 -l smallClassic -a 'discretization=small'

layout:  smallClassic
Training episode: 0 Reward: -501.0 Number of actions: 44 Score: -364.0
Training episode: 1 Reward: -501.0 Number of actions: 206 Score: -546.0
Training episode: 2 Reward: -501.0 Number of actions: 49 Score: -399.0
Training episode: 3 Reward: -491.0 Number of actions: 8 Score: -448.0
Training episode: 4 Reward: -491.0 Number of actions: 11 Score: -431.0
Training episode: 5 Reward: -501.0 Number of actions: 11 Score: -431.0
Training episode: 6 Reward: -501.0 Number of actions: 11 Score: -431.0
Training episode: 7 Reward: -501.0 Number of actions: 15 Score: -415.0
Training episode: 8 Reward: -491.0 Number of actions: 12 Score: -392.0
Training episode: 9 Reward: -491.0 Number of actions: 9 Score: -449.0
Training episode: 10 Reward: -491.0 Number of actions: 7 Score: -447.0
Training episode: 11 Reward: -501.0 Number of actions: 47 Score: -367.0
Training episode: 12 Reward: -501.0 Number of actions: 215 Score: -525.0
Training episode: 13 Reward: -501.0 Number of actions

Training episode: 113 Reward: -501.0 Number of actions: 22 Score: -392.0
Training episode: 114 Reward: -501.0 Number of actions: 28 Score: -368.0
Training episode: 115 Reward: -501.0 Number of actions: 8 Score: -448.0
Training episode: 116 Reward: -501.0 Number of actions: 12 Score: -472.0
Training episode: 117 Reward: -501.0 Number of actions: 185 Score: -445.0
Training episode: 118 Reward: -501.0 Number of actions: 26 Score: -376.0
Training episode: 119 Reward: -491.0 Number of actions: 7 Score: -447.0
Training episode: 120 Reward: -501.0 Number of actions: 117 Score: -387.0
Training episode: 121 Reward: -501.0 Number of actions: 50 Score: -310.0
Training episode: 122 Reward: -501.0 Number of actions: 37 Score: -387.0
Training episode: 123 Reward: -501.0 Number of actions: 22 Score: -322.0
Training episode: 124 Reward: -501.0 Number of actions: 50 Score: -380.0
Training episode: 125 Reward: -501.0 Number of actions: 65 Score: -355.0
Training episode: 126 Reward: -501.0 Number of acti

Training episode: 224 Reward: -501.0 Number of actions: 101 Score: -361.0
Training episode: 225 Reward: -491.0 Number of actions: 22 Score: -312.0
Training episode: 226 Reward: -501.0 Number of actions: 34 Score: -344.0
Training episode: 227 Reward: -501.0 Number of actions: 13 Score: -393.0
Training episode: 228 Reward: -501.0 Number of actions: 50 Score: -400.0
Training episode: 229 Reward: -501.0 Number of actions: 20 Score: -360.0
Training episode: 230 Reward: -501.0 Number of actions: 20 Score: -350.0
Training episode: 231 Reward: -501.0 Number of actions: 56 Score: -366.0
Training episode: 232 Reward: -501.0 Number of actions: 27 Score: -447.0
Training episode: 233 Reward: -491.0 Number of actions: 17 Score: -347.0
Training episode: 234 Reward: -491.0 Number of actions: 9 Score: -419.0
Training episode: 235 Reward: -501.0 Number of actions: 30 Score: -340.0
Training episode: 236 Reward: -501.0 Number of actions: 20 Score: -430.0
Training episode: 237 Reward: -501.0 Number of acti

Training episode: 337 Reward: -501.0 Number of actions: 17 Score: -397.0
Training episode: 338 Reward: -501.0 Number of actions: 57 Score: -307.0
Training episode: 339 Reward: -501.0 Number of actions: 9 Score: -459.0
Training episode: 340 Reward: -501.0 Number of actions: 109 Score: -349.0
Training episode: 341 Reward: -501.0 Number of actions: 95 Score: -335.0
Training episode: 342 Reward: -501.0 Number of actions: 101 Score: -361.0
Training episode: 343 Reward: -501.0 Number of actions: 20 Score: -330.0
Training episode: 344 Reward: -501.0 Number of actions: 17 Score: -357.0
Training episode: 345 Reward: -501.0 Number of actions: 85 Score: -335.0
Training episode: 346 Reward: -501.0 Number of actions: 15 Score: -375.0
Training episode: 347 Reward: -501.0 Number of actions: 170 Score: -220.0
Training episode: 348 Reward: -501.0 Number of actions: 32 Score: -402.0
Training episode: 349 Reward: -501.0 Number of actions: 78 Score: -128.0
Training episode: 350 Reward: -501.0 Number of ac

Training episode: 448 Reward: -501.0 Number of actions: 26 Score: -336.0
Training episode: 449 Reward: -501.0 Number of actions: 205 Score: -505.0
Training episode: 450 Reward: -501.0 Number of actions: 40 Score: -300.0
Training episode: 451 Reward: -491.0 Number of actions: 18 Score: -378.0
Training episode: 452 Reward: -501.0 Number of actions: 16 Score: -396.0
Training episode: 453 Reward: -501.0 Number of actions: 72 Score: -372.0
Training episode: 454 Reward: -501.0 Number of actions: 34 Score: -294.0
Training episode: 455 Reward: -501.0 Number of actions: 93 Score: -383.0
Training episode: 456 Reward: -501.0 Number of actions: 19 Score: -339.0
Training episode: 457 Reward: -501.0 Number of actions: 22 Score: -372.0
Training episode: 458 Reward: -501.0 Number of actions: 11 Score: -411.0
Training episode: 459 Reward: -501.0 Number of actions: 81 Score: 79.0
Training episode: 460 Reward: -501.0 Number of actions: 15 Score: -425.0
Training episode: 461 Reward: -491.0 Number of actio

...

Training episode: 29537 Reward: 509.0 Number of actions: 85 Score: 1165.0
Training episode: 29538 Reward: -501.0 Number of actions: 78 Score: -98.0
Training episode: 29539 Reward: -501.0 Number of actions: 83 Score: -273.0
Training episode: 29540 Reward: 509.0 Number of actions: 96 Score: 954.0
Training episode: 29541 Reward: 509.0 Number of actions: 70 Score: 980.0
Training episode: 29542 Reward: 509.0 Number of actions: 86 Score: 964.0
Training episode: 29543 Reward: -501.0 Number of actions: 100 Score: -60.0
Training episode: 29544 Reward: -501.0 Number of actions: 69 Score: -109.0
Training episode: 29545 Reward: 509.0 Number of actions: 119 Score: 931.0
Training episode: 29546 Reward: -501.0 Number of actions: 57 Score: -167.0
Training episode: 29547 Reward: -491.0 Number of actions: 41 Score: -251.0
Training episode: 29548 Reward: 509.0 Number of actions: 73 Score: 977.0
Training episode: 29549 Reward: 509.0 Number of actions: 108 Score: 1142.0
Training episode: 29550 Reward: 509.

Training episode: 29646 Reward: 509.0 Number of actions: 126 Score: 924.0
Training episode: 29647 Reward: 509.0 Number of actions: 81 Score: 969.0
Training episode: 29648 Reward: 509.0 Number of actions: 83 Score: 967.0
Training episode: 29649 Reward: -501.0 Number of actions: 106 Score: 94.0
Training episode: 29650 Reward: 509.0 Number of actions: 89 Score: 961.0
Training episode: 29651 Reward: 509.0 Number of actions: 108 Score: 942.0
Training episode: 29652 Reward: -501.0 Number of actions: 54 Score: -174.0
Training episode: 29653 Reward: -501.0 Number of actions: 109 Score: -69.0
Training episode: 29654 Reward: -501.0 Number of actions: 84 Score: -84.0
Training episode: 29655 Reward: -501.0 Number of actions: 21 Score: -371.0
Training episode: 29656 Reward: -501.0 Number of actions: 65 Score: -105.0
Training episode: 29657 Reward: 509.0 Number of actions: 102 Score: 1148.0
Training episode: 29658 Reward: -501.0 Number of actions: 367 Score: -187.0
Training episode: 29659 Reward: -5

Training episode: 29755 Reward: -501.0 Number of actions: 186 Score: 24.0
Training episode: 29756 Reward: 509.0 Number of actions: 124 Score: 1126.0
Training episode: 29757 Reward: -501.0 Number of actions: 64 Score: -264.0
Training episode: 29758 Reward: -501.0 Number of actions: 81 Score: -131.0
Training episode: 29759 Reward: 509.0 Number of actions: 100 Score: 950.0
Training episode: 29760 Reward: -501.0 Number of actions: 89 Score: -79.0
Training episode: 29761 Reward: 509.0 Number of actions: 77 Score: 973.0
Training episode: 29762 Reward: -501.0 Number of actions: 38 Score: -288.0
Training episode: 29763 Reward: -501.0 Number of actions: 137 Score: -107.0
Training episode: 29764 Reward: -501.0 Number of actions: 85 Score: -205.0
Training episode: 29765 Reward: -501.0 Number of actions: 79 Score: -69.0
Training episode: 29766 Reward: 509.0 Number of actions: 89 Score: 1161.0
Training episode: 29767 Reward: -501.0 Number of actions: 109 Score: -109.0
Training episode: 29768 Reward

Training episode: 29864 Reward: -501.0 Number of actions: 79 Score: -229.0
Training episode: 29865 Reward: -501.0 Number of actions: 171 Score: -131.0
Training episode: 29866 Reward: -501.0 Number of actions: 65 Score: -55.0
Training episode: 29867 Reward: 509.0 Number of actions: 80 Score: 970.0
Training episode: 29868 Reward: -501.0 Number of actions: 102 Score: -72.0
Training episode: 29869 Reward: -501.0 Number of actions: 24 Score: -324.0
Training episode: 29870 Reward: 509.0 Number of actions: 78 Score: 972.0
Training episode: 29871 Reward: -501.0 Number of actions: 98 Score: 142.0
Training episode: 29872 Reward: -501.0 Number of actions: 39 Score: -309.0
Training episode: 29873 Reward: -501.0 Number of actions: 46 Score: -296.0
Training episode: 29874 Reward: -501.0 Number of actions: 78 Score: -148.0
Training episode: 29875 Reward: -501.0 Number of actions: 82 Score: -192.0
Training episode: 29876 Reward: 509.0 Number of actions: 123 Score: 927.0
Training episode: 29877 Reward:

Training episode: 29973 Reward: 509.0 Number of actions: 95 Score: 955.0
Training episode: 29974 Reward: -501.0 Number of actions: 103 Score: -103.0
Training episode: 29975 Reward: 509.0 Number of actions: 129 Score: 1121.0
Training episode: 29976 Reward: -491.0 Number of actions: 43 Score: -243.0
Training episode: 29977 Reward: 509.0 Number of actions: 83 Score: 1167.0
Training episode: 29978 Reward: 509.0 Number of actions: 71 Score: 1179.0
Training episode: 29979 Reward: 509.0 Number of actions: 109 Score: 941.0
Training episode: 29980 Reward: 509.0 Number of actions: 70 Score: 980.0
Training episode: 29981 Reward: 509.0 Number of actions: 85 Score: 965.0
Training episode: 29982 Reward: -501.0 Number of actions: 41 Score: -271.0
Training episode: 29983 Reward: 509.0 Number of actions: 96 Score: 1154.0
Training episode: 29984 Reward: 509.0 Number of actions: 90 Score: 1560.0
Training episode: 29985 Reward: 509.0 Number of actions: 78 Score: 972.0
Training episode: 29986 Reward: -501.

In [7]:
!cd rl_algorithm/search && python3 pacman.py -p QLearningAgent -x 30000 -n 30010 -l mediumClassic -a 'discretization=medium'

layout:  mediumClassic
Training episode: 0 Reward: -501.0 Number of actions: 85 Score: -415.0
Training episode: 1 Reward: -501.0 Number of actions: 139 Score: -419.0
Training episode: 2 Reward: -501.0 Number of actions: 27 Score: -407.0
Training episode: 3 Reward: -501.0 Number of actions: 161 Score: -421.0
Training episode: 4 Reward: -501.0 Number of actions: 12 Score: -422.0
Training episode: 5 Reward: -501.0 Number of actions: 24 Score: -404.0
Training episode: 6 Reward: -491.0 Number of actions: 9 Score: -419.0
Training episode: 7 Reward: -501.0 Number of actions: 10 Score: -430.0
Training episode: 8 Reward: -501.0 Number of actions: 14 Score: -384.0
Training episode: 9 Reward: -501.0 Number of actions: 168 Score: -438.0
Training episode: 10 Reward: -501.0 Number of actions: 22 Score: -392.0
Training episode: 11 Reward: -501.0 Number of actions: 158 Score: -438.0
Training episode: 12 Reward: -501.0 Number of actions: 15 Score: -375.0
Training episode: 13 Reward: -501.0 Number of ac

Training episode: 112 Reward: -501.0 Number of actions: 192 Score: -462.0
Training episode: 113 Reward: -491.0 Number of actions: 47 Score: -197.0
Training episode: 114 Reward: -491.0 Number of actions: 73 Score: -333.0
Training episode: 115 Reward: -491.0 Number of actions: 20 Score: -350.0
Training episode: 116 Reward: -501.0 Number of actions: 214 Score: -504.0
Training episode: 117 Reward: -501.0 Number of actions: 63 Score: -373.0
Training episode: 118 Reward: -491.0 Number of actions: 27 Score: -327.0
Training episode: 119 Reward: -501.0 Number of actions: 64 Score: -294.0
Training episode: 120 Reward: -501.0 Number of actions: 33 Score: -323.0
Training episode: 121 Reward: -491.0 Number of actions: 9 Score: -419.0
Training episode: 122 Reward: -501.0 Number of actions: 187 Score: -447.0
Training episode: 123 Reward: -491.0 Number of actions: 346 Score: -606.0
Training episode: 124 Reward: -501.0 Number of actions: 24 Score: -384.0
Training episode: 125 Reward: -501.0 Number of a

Training episode: 223 Reward: -501.0 Number of actions: 256 Score: -326.0
Training episode: 224 Reward: -501.0 Number of actions: 19 Score: -389.0
Training episode: 225 Reward: -501.0 Number of actions: 84 Score: -314.0
Training episode: 226 Reward: -501.0 Number of actions: 15 Score: -405.0
Training episode: 227 Reward: -501.0 Number of actions: 53 Score: -303.0
Training episode: 228 Reward: -501.0 Number of actions: 72 Score: -352.0
Training episode: 229 Reward: -501.0 Number of actions: 88 Score: -268.0
Training episode: 230 Reward: -491.0 Number of actions: 22 Score: -322.0
Training episode: 231 Reward: -501.0 Number of actions: 32 Score: -312.0
Training episode: 232 Reward: -501.0 Number of actions: 140 Score: -180.0
Training episode: 233 Reward: -501.0 Number of actions: 21 Score: -381.0
Training episode: 234 Reward: -501.0 Number of actions: 78 Score: -338.0
Training episode: 235 Reward: -501.0 Number of actions: 165 Score: -395.0
Training episode: 236 Reward: -491.0 Number of a

Training episode: 334 Reward: -501.0 Number of actions: 208 Score: -378.0
Training episode: 335 Reward: -501.0 Number of actions: 23 Score: -353.0
Training episode: 336 Reward: -501.0 Number of actions: 20 Score: -380.0
Training episode: 337 Reward: -501.0 Number of actions: 53 Score: -303.0
Training episode: 338 Reward: -501.0 Number of actions: 104 Score: -284.0
Training episode: 339 Reward: -501.0 Number of actions: 59 Score: -249.0
Training episode: 340 Reward: -501.0 Number of actions: 80 Score: -290.0
Training episode: 341 Reward: -491.0 Number of actions: 74 Score: -204.0
Training episode: 342 Reward: -501.0 Number of actions: 183 Score: -423.0
Training episode: 343 Reward: -501.0 Number of actions: 16 Score: -386.0
Training episode: 344 Reward: -501.0 Number of actions: 165 Score: -175.0
Training episode: 345 Reward: -501.0 Number of actions: 156 Score: -216.0
Training episode: 346 Reward: -501.0 Number of actions: 61 Score: -121.0
Training episode: 347 Reward: -501.0 Number of

Training episode: 445 Reward: -501.0 Number of actions: 53 Score: -313.0
Training episode: 446 Reward: -491.0 Number of actions: 33 Score: -343.0
Training episode: 447 Reward: -501.0 Number of actions: 20 Score: -380.0
Training episode: 448 Reward: -501.0 Number of actions: 161 Score: 109.0
Training episode: 449 Reward: -501.0 Number of actions: 195 Score: -135.0
Training episode: 450 Reward: -501.0 Number of actions: 40 Score: -290.0
Training episode: 451 Reward: -501.0 Number of actions: 31 Score: -311.0
Training episode: 452 Reward: -501.0 Number of actions: 117 Score: -307.0
Training episode: 453 Reward: -501.0 Number of actions: 16 Score: -406.0
Training episode: 454 Reward: -501.0 Number of actions: 36 Score: -276.0
Training episode: 455 Reward: -501.0 Number of actions: 24 Score: -334.0
Training episode: 456 Reward: -501.0 Number of actions: 53 Score: -293.0
Training episode: 457 Reward: -501.0 Number of actions: 278 Score: -48.0
Training episode: 458 Reward: -501.0 Number of ac

...

Training episode: 29510 Reward: -501.0 Number of actions: 255 Score: 365.0
Training episode: 29511 Reward: -501.0 Number of actions: 303 Score: 547.0
Training episode: 29512 Reward: -501.0 Number of actions: 364 Score: -204.0
Training episode: 29513 Reward: 509.0 Number of actions: 237 Score: 1233.0
Training episode: 29514 Reward: 509.0 Number of actions: 157 Score: 1513.0
Training episode: 29515 Reward: -501.0 Number of actions: 110 Score: 160.0
Training episode: 29516 Reward: -501.0 Number of actions: 160 Score: 80.0
Training episode: 29517 Reward: -501.0 Number of actions: 117 Score: 103.0
Training episode: 29518 Reward: 509.0 Number of actions: 238 Score: 1432.0
Training episode: 29519 Reward: 509.0 Number of actions: 206 Score: 1664.0
Training episode: 29520 Reward: 509.0 Number of actions: 184 Score: 1286.0
Training episode: 29521 Reward: -501.0 Number of actions: 66 Score: -126.0
Training episode: 29522 Reward: -501.0 Number of actions: 165 Score: 305.0
Training episode: 29523 R

Training episode: 29618 Reward: -501.0 Number of actions: 89 Score: 31.0
Training episode: 29619 Reward: 509.0 Number of actions: 173 Score: 1297.0
Training episode: 29620 Reward: 509.0 Number of actions: 349 Score: 1121.0
Training episode: 29621 Reward: 509.0 Number of actions: 173 Score: 1297.0
Training episode: 29622 Reward: -501.0 Number of actions: 27 Score: -327.0
Training episode: 29623 Reward: 509.0 Number of actions: 188 Score: 1482.0
Training episode: 29624 Reward: 509.0 Number of actions: 194 Score: 1476.0
Training episode: 29625 Reward: 509.0 Number of actions: 195 Score: 1475.0
Training episode: 29626 Reward: -501.0 Number of actions: 139 Score: 251.0
Training episode: 29627 Reward: -501.0 Number of actions: 103 Score: 167.0
Training episode: 29628 Reward: 509.0 Number of actions: 183 Score: 1287.0
Training episode: 29629 Reward: 509.0 Number of actions: 239 Score: 1231.0
Training episode: 29630 Reward: -501.0 Number of actions: 80 Score: -20.0
Training episode: 29631 Rewa

Training episode: 29726 Reward: -501.0 Number of actions: 141 Score: -181.0
Training episode: 29727 Reward: -501.0 Number of actions: 181 Score: -21.0
Training episode: 29728 Reward: 509.0 Number of actions: 183 Score: 1287.0
Training episode: 29729 Reward: 509.0 Number of actions: 297 Score: 1173.0
Training episode: 29730 Reward: -501.0 Number of actions: 108 Score: 32.0
Training episode: 29731 Reward: 509.0 Number of actions: 333 Score: 1337.0
Training episode: 29732 Reward: 509.0 Number of actions: 201 Score: 1269.0
Training episode: 29733 Reward: 509.0 Number of actions: 198 Score: 1672.0
Training episode: 29734 Reward: -491.0 Number of actions: 77 Score: 193.0
Training episode: 29735 Reward: 509.0 Number of actions: 212 Score: 1258.0
Training episode: 29736 Reward: -501.0 Number of actions: 97 Score: 133.0
Training episode: 29737 Reward: -501.0 Number of actions: 62 Score: -172.0
Training episode: 29738 Reward: -501.0 Number of actions: 340 Score: 110.0
Training episode: 29739 Rew

Training episode: 29834 Reward: -501.0 Number of actions: 132 Score: 68.0
Training episode: 29835 Reward: -501.0 Number of actions: 27 Score: -317.0
Training episode: 29836 Reward: -501.0 Number of actions: 65 Score: -165.0
Training episode: 29837 Reward: 509.0 Number of actions: 148 Score: 1522.0
Training episode: 29838 Reward: 509.0 Number of actions: 237 Score: 1233.0
Training episode: 29839 Reward: 509.0 Number of actions: 203 Score: 1467.0
Training episode: 29840 Reward: -501.0 Number of actions: 234 Score: 416.0
Training episode: 29841 Reward: 509.0 Number of actions: 293 Score: 1377.0
Training episode: 29842 Reward: 509.0 Number of actions: 222 Score: 1448.0
Training episode: 29843 Reward: -501.0 Number of actions: 197 Score: 223.0
Training episode: 29844 Reward: -501.0 Number of actions: 161 Score: 449.0
Training episode: 29845 Reward: 509.0 Number of actions: 366 Score: 1104.0
Training episode: 29846 Reward: 509.0 Number of actions: 219 Score: 1251.0
Training episode: 29847 Re

Training episode: 29942 Reward: -501.0 Number of actions: 203 Score: 397.0
Training episode: 29943 Reward: -501.0 Number of actions: 164 Score: 226.0
Training episode: 29944 Reward: 509.0 Number of actions: 266 Score: 1404.0
Training episode: 29945 Reward: 509.0 Number of actions: 184 Score: 1686.0
Training episode: 29946 Reward: -501.0 Number of actions: 181 Score: 209.0
Training episode: 29947 Reward: -501.0 Number of actions: 322 Score: 138.0
Training episode: 29948 Reward: 509.0 Number of actions: 206 Score: 1264.0
Training episode: 29949 Reward: -501.0 Number of actions: 249 Score: 211.0
Training episode: 29950 Reward: -501.0 Number of actions: 158 Score: 212.0
Training episode: 29951 Reward: -501.0 Number of actions: 193 Score: 257.0
Training episode: 29952 Reward: 509.0 Number of actions: 219 Score: 1251.0
Training episode: 29953 Reward: -501.0 Number of actions: 111 Score: -81.0
Training episode: 29954 Reward: 509.0 Number of actions: 226 Score: 1244.0
Training episode: 29955 R

In [8]:
!cd rl_algorithm/search && python3 pacman.py -p QLearningAgent -x 30000 -n 30010 -l originalClassic -a 'discretization=original'

layout:  originalClassic
Training episode: 0 Reward: -501.0 Number of actions: 29 Score: -449.0
Training episode: 1 Reward: -501.0 Number of actions: 203 Score: -333.0
Training episode: 2 Reward: -501.0 Number of actions: 77 Score: -407.0
Training episode: 3 Reward: -501.0 Number of actions: 83 Score: -433.0
Training episode: 4 Reward: -491.0 Number of actions: 62 Score: -232.0
Training episode: 5 Reward: -501.0 Number of actions: 301 Score: -611.0
Training episode: 6 Reward: -501.0 Number of actions: 217 Score: -567.0
Training episode: 7 Reward: -491.0 Number of actions: 24 Score: -304.0
Training episode: 8 Reward: -501.0 Number of actions: 120 Score: -150.0
Training episode: 9 Reward: -501.0 Number of actions: 202 Score: -262.0
Training episode: 10 Reward: -501.0 Number of actions: 250 Score: -510.0
Training episode: 11 Reward: -491.0 Number of actions: 18 Score: -358.0
Training episode: 12 Reward: -501.0 Number of actions: 94 Score: -304.0
Training episode: 13 Reward: -501.0 Number 

Training episode: 112 Reward: -501.0 Number of actions: 143 Score: -43.0
Training episode: 113 Reward: -501.0 Number of actions: 267 Score: 143.0
Training episode: 114 Reward: -501.0 Number of actions: 268 Score: -88.0
Training episode: 115 Reward: -501.0 Number of actions: 384 Score: -174.0
Training episode: 116 Reward: -501.0 Number of actions: 69 Score: -389.0
Training episode: 117 Reward: -501.0 Number of actions: 175 Score: 165.0
Training episode: 118 Reward: -501.0 Number of actions: 379 Score: 221.0
Training episode: 119 Reward: -501.0 Number of actions: 203 Score: -183.0
Training episode: 120 Reward: -501.0 Number of actions: 187 Score: -487.0
Training episode: 121 Reward: -501.0 Number of actions: 136 Score: -316.0
Training episode: 122 Reward: -501.0 Number of actions: 712 Score: -312.0
Training episode: 123 Reward: -501.0 Number of actions: 406 Score: -176.0
Training episode: 124 Reward: -501.0 Number of actions: 165 Score: 165.0
Training episode: 125 Reward: -501.0 Number o

Training episode: 223 Reward: -501.0 Number of actions: 108 Score: -88.0
Training episode: 224 Reward: -501.0 Number of actions: 52 Score: -272.0
Training episode: 225 Reward: -501.0 Number of actions: 44 Score: -294.0
Training episode: 226 Reward: -501.0 Number of actions: 61 Score: -111.0
Training episode: 227 Reward: -501.0 Number of actions: 324 Score: 216.0
Training episode: 228 Reward: -491.0 Number of actions: 35 Score: -335.0
Training episode: 229 Reward: -501.0 Number of actions: 88 Score: -128.0
Training episode: 230 Reward: -501.0 Number of actions: 179 Score: -319.0
Training episode: 231 Reward: -501.0 Number of actions: 117 Score: 223.0
Training episode: 232 Reward: -501.0 Number of actions: 116 Score: 174.0
Training episode: 233 Reward: -501.0 Number of actions: 166 Score: -56.0
Training episode: 234 Reward: -491.0 Number of actions: 39 Score: -309.0
Training episode: 235 Reward: -501.0 Number of actions: 809 Score: -469.0
Training episode: 236 Reward: -501.0 Number of ac

Training episode: 334 Reward: -491.0 Number of actions: 62 Score: -152.0
Training episode: 335 Reward: -501.0 Number of actions: 63 Score: -133.0
Training episode: 336 Reward: -501.0 Number of actions: 91 Score: -141.0
Training episode: 337 Reward: -501.0 Number of actions: 56 Score: -196.0
Training episode: 338 Reward: -501.0 Number of actions: 136 Score: -66.0
Training episode: 339 Reward: -501.0 Number of actions: 153 Score: 137.0
Training episode: 340 Reward: -501.0 Number of actions: 120 Score: 20.0
Training episode: 341 Reward: -501.0 Number of actions: 51 Score: -171.0
Training episode: 342 Reward: -501.0 Number of actions: 180 Score: 150.0
Training episode: 343 Reward: -501.0 Number of actions: 72 Score: 88.0
Training episode: 344 Reward: -501.0 Number of actions: 213 Score: 37.0
Training episode: 345 Reward: -501.0 Number of actions: 43 Score: -293.0
Training episode: 346 Reward: -501.0 Number of actions: 157 Score: -317.0
Training episode: 347 Reward: -501.0 Number of actions

Training episode: 445 Reward: -501.0 Number of actions: 115 Score: -155.0
Training episode: 446 Reward: -501.0 Number of actions: 305 Score: 45.0
Training episode: 447 Reward: -501.0 Number of actions: 50 Score: -310.0
Training episode: 448 Reward: -501.0 Number of actions: 38 Score: -358.0
Training episode: 449 Reward: -501.0 Number of actions: 147 Score: -167.0
Training episode: 450 Reward: -501.0 Number of actions: 76 Score: -226.0
Training episode: 451 Reward: -501.0 Number of actions: 116 Score: -76.0
Training episode: 452 Reward: -491.0 Number of actions: 136 Score: 64.0
Training episode: 453 Reward: -501.0 Number of actions: 66 Score: -146.0
Training episode: 454 Reward: -501.0 Number of actions: 49 Score: -159.0
Training episode: 455 Reward: -501.0 Number of actions: 116 Score: 34.0
Training episode: 456 Reward: -501.0 Number of actions: 65 Score: -315.0
Training episode: 457 Reward: -501.0 Number of actions: 94 Score: -4.0
Training episode: 458 Reward: -501.0 Number of actions

...

Training episode: 29546 Reward: -501.0 Number of actions: 246 Score: 134.0
Training episode: 29547 Reward: -501.0 Number of actions: 83 Score: -153.0
Training episode: 29548 Reward: -1001.0 Number of actions: 239 Score: -409.0
Training episode: 29549 Reward: -501.0 Number of actions: 60 Score: -220.0
Training episode: 29550 Reward: -501.0 Number of actions: 517 Score: 293.0
Training episode: 29551 Reward: -501.0 Number of actions: 651 Score: 69.0
Training episode: 29552 Reward: -501.0 Number of actions: 641 Score: 79.0
Training episode: 29553 Reward: -501.0 Number of actions: 480 Score: 560.0
Training episode: 29554 Reward: -501.0 Number of actions: 111 Score: 169.0
Training episode: 29555 Reward: -501.0 Number of actions: 277 Score: 313.0
Training episode: 29556 Reward: -501.0 Number of actions: 193 Score: -63.0
Training episode: 29557 Reward: -501.0 Number of actions: 423 Score: 177.0
Training episode: 29558 Reward: -501.0 Number of actions: 408 Score: 692.0
Training episode: 29559 R

Training episode: 29654 Reward: -501.0 Number of actions: 317 Score: 213.0
Training episode: 29655 Reward: -501.0 Number of actions: 653 Score: 557.0
Training episode: 29656 Reward: -501.0 Number of actions: 126 Score: -156.0
Training episode: 29657 Reward: -501.0 Number of actions: 156 Score: 84.0
Training episode: 29658 Reward: -501.0 Number of actions: 68 Score: -178.0
Training episode: 29659 Reward: -501.0 Number of actions: 112 Score: -72.0
Training episode: 29660 Reward: -501.0 Number of actions: 845 Score: -195.0
Training episode: 29661 Reward: -501.0 Number of actions: 754 Score: 1036.0
Training episode: 29662 Reward: -501.0 Number of actions: 306 Score: 114.0
Training episode: 29663 Reward: -501.0 Number of actions: 350 Score: 650.0
Training episode: 29664 Reward: -501.0 Number of actions: 279 Score: 121.0
Training episode: 29665 Reward: -501.0 Number of actions: 515 Score: 995.0
Training episode: 29666 Reward: -501.0 Number of actions: 160 Score: 60.0
Training episode: 29667 

Training episode: 29762 Reward: -501.0 Number of actions: 37 Score: -237.0
Training episode: 29763 Reward: -501.0 Number of actions: 268 Score: 422.0
Training episode: 29764 Reward: -501.0 Number of actions: 111 Score: -131.0
Training episode: 29765 Reward: -501.0 Number of actions: 56 Score: -226.0
Training episode: 29766 Reward: -501.0 Number of actions: 105 Score: 55.0
Training episode: 29767 Reward: -501.0 Number of actions: 246 Score: 194.0
Training episode: 29768 Reward: -501.0 Number of actions: 295 Score: 555.0
Training episode: 29769 Reward: -501.0 Number of actions: 479 Score: 341.0
Training episode: 29770 Reward: -501.0 Number of actions: 418 Score: 702.0
Training episode: 29771 Reward: -501.0 Number of actions: 141 Score: 39.0
Training episode: 29772 Reward: -501.0 Number of actions: 377 Score: 543.0
Training episode: 29773 Reward: -501.0 Number of actions: 238 Score: 52.0
Training episode: 29774 Reward: -501.0 Number of actions: 310 Score: 410.0
Training episode: 29775 Rew

Training episode: 29870 Reward: -501.0 Number of actions: 823 Score: 837.0
Training episode: 29871 Reward: -501.0 Number of actions: 249 Score: 121.0
Training episode: 29872 Reward: -501.0 Number of actions: 287 Score: 393.0
Training episode: 29873 Reward: -501.0 Number of actions: 168 Score: 182.0
Training episode: 29874 Reward: -501.0 Number of actions: 369 Score: 431.0
Training episode: 29875 Reward: -501.0 Number of actions: 477 Score: 843.0
Training episode: 29876 Reward: -501.0 Number of actions: 374 Score: 266.0
Training episode: 29877 Reward: -501.0 Number of actions: 288 Score: 262.0
Training episode: 29878 Reward: -501.0 Number of actions: 378 Score: 552.0
Training episode: 29879 Reward: -501.0 Number of actions: 144 Score: -104.0
Training episode: 29880 Reward: -501.0 Number of actions: 556 Score: 564.0
Training episode: 29881 Reward: -501.0 Number of actions: 624 Score: 1226.0
Training episode: 29882 Reward: -501.0 Number of actions: 171 Score: 129.0
Training episode: 29883

Training episode: 29978 Reward: -501.0 Number of actions: 85 Score: -255.0
Training episode: 29979 Reward: -501.0 Number of actions: 366 Score: 784.0
Training episode: 29980 Reward: -501.0 Number of actions: 176 Score: -256.0
Training episode: 29981 Reward: -501.0 Number of actions: 638 Score: 82.0
Training episode: 29982 Reward: -501.0 Number of actions: 165 Score: 55.0
Training episode: 29983 Reward: -501.0 Number of actions: 506 Score: 654.0
Training episode: 29984 Reward: -501.0 Number of actions: 360 Score: -140.0
Training episode: 29985 Reward: -501.0 Number of actions: 171 Score: 299.0
Training episode: 29986 Reward: -501.0 Number of actions: 334 Score: 646.0
Training episode: 29987 Reward: -501.0 Number of actions: 324 Score: 316.0
Training episode: 29988 Reward: -501.0 Number of actions: 143 Score: 147.0
Training episode: 29989 Reward: -501.0 Number of actions: 274 Score: 506.0
Training episode: 29990 Reward: -501.0 Number of actions: 379 Score: 181.0
Training episode: 29991 R

## Contribuições
<br>
O membro do grupo <b>Lucas Zanco Ladeira</b> contribuiu com toda a implementação, validação e escrita da parte I deste trabalho.

O membro do grupo <b>Rafael Scherer</b> contribuiu com toda a implementação, validação e escrita da parte II deste trabalho.